# Visualization with pyrosetta.distributed.viewer

The Viewer quickly renders .pdb files, dynamically instantiating Pose objects if required
for certain visualization modules (matching the name "viewer.set*"). So when adding
visualization modules to the Viewer or using presets, passing Pose or PackedPose objects to the
Viewer is suggested for quicker rendering. If a Pose object or list, tuple, or set of Pose
objects are provided to the Viewer, the Pose(s) pointer location(s) in memory remain fixed, and so
the Viewer can dynamically update upon Pose conformational changes by calling the show() method.
The Viewer applies visualization modules in the same order they are added (from left to right),
so layering different styles (and ResidueSelectors) on top of one another becomes possible.
The user must have already initialized PyRosetta providing .params files for any ligands and 
non-canonical residues in the Pose, otherwise pyrosetta.distributed automatically initializes
PyRosetta with default options.

In [32]:
import glob
import logging
logging.basicConfig(level=logging.INFO)
import pyrosetta
import pyrosetta.distributed.io as io
import pyrosetta.distributed.viewer as viewer
import sys

if 'google.colab' in sys.modules:
    !pip install pyrosettacolabsetup
    import pyrosettacolabsetup
    pyrosettacolabsetup.setup()
    print ("Notebook is set for PyRosetta use in Colab.  Have fun!")

Show basic line representation of .pdbfile on disk:

```
view = viewer.init("path/to/my.pdb")
view.show()
```

Show basic stick representation of Pose or PackedPose objects in memory:

In [38]:
flags = """
-auto_setup_metals 1
-detect_disulf 1
"""
pyrosetta.distributed.init(flags)

pose = pyrosetta.io.pose_from_file("inputs/3EK4.pdb")

view = viewer.init(pose, window_size=(800, 600))
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

To show basic cartoon representation, add `viewer.setStyle()`:

In [39]:
view = viewer.init(pose, window_size=(800, 600)) + viewer.setStyle()
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

To show ligands, non-conanical amino acids, metals, etc., `viewer.setStyle()` (and several other `viewer.set*` objects) optionally accept PyRosetta `ResidueSelectors`.

`pyrosetta.distributed.viewer` passes the `Pose`'s PDB numbering of selected residues to `py3dmol` for macromolecular rendering. Also, one may layer any visualization modules with any `ResidueSelectors` in the order they are summed (from left to right). In this case:

In [47]:
metals_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
     pyrosetta.rosetta.core.chemical.ResidueProperty(31)
)
ligands_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
     pyrosetta.rosetta.core.chemical.ResidueProperty(2)
)

view = viewer.init(pose, window_size=(800, 600)) \
+ viewer.setStyle() \
+ viewer.setStyle(residue_selector=ligands_selector, style="stick", colorscheme="magentaCarbon", radius=0.5) \
+ viewer.setStyle(residue_selector=metals_selector, style="sphere", colorscheme="chainHetatm", radius=1.5)

 1. `viewer.setStyle()` layers the cartoon backbone and stick side-chain representation by default
 2. `viewer.setStyle(residue_selector=ligands_selector, style="stick", colorscheme="magentaCarbon", radius=0.5)` layers any residue with the `LIGAND` property a 0.5 radius stick with magenta carbon atoms.
 3. `viewer.setStyle(residue_selector=metals_selector, style="sphere", colorscheme="chainHetatm", radius=1.5)` layers any residue with the `METAL` property a 1.5 radius sphere with the `py3dmol` color scheme "chainHetatm". 

In [48]:
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Show many Poses in memory using the interactive slider widget:

In [52]:
poses = [pyrosetta.io.pose_from_sequence("TESTVIEWER" * i) for i in range(1, 10)]

view = viewer.init(poses, continuous_update=True)
view.add(viewer.setStyle(colorscheme="lightgreyCarbon"))
view.add(viewer.setHydrogenBonds(radius=1, dashed=False))
view()

interactive(children=(IntSlider(value=0, description='Decoys', max=8), Output()), _dom_classes=('widget-intera…

<function pyrosetta.distributed.viewer.core.Viewer.show.<locals>.view(i=0)>

Below, layer a `ResidueSelector` of residues with `ResidueProperty.POLAR`, then hydrogen atoms, hydrogen bonds, and disulfide bonds:

In [55]:
polar_residue_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
    pyrosetta.rosetta.core.chemical.ResidueProperty(52)
)
view = viewer.init(io.to_packed(pose))
view.add(viewer.setStyle(radius=0.1))
view.add(viewer.setStyle(residue_selector=polar_residue_selector, colorscheme="whiteCarbon", radius=0.25, label=False))
view.add(viewer.setHydrogens(color="white", polar_only=True, radius=0.1))
view.add(viewer.setHydrogenBonds(color="black"))
view.add(viewer.setDisulfides(radius=0.1))
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [62]:
view = sum(
    [
        viewer.init(pose),
        viewer.setStyle(cartoon=False, style="sphere", radius=1.5, colorscheme="darkgreyCarbon"),
        viewer.setZoom(factor=0.95)
    ]
)
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
chA = pyrosetta.rosetta.core.select.residue_selector.ChainSelector("A")
chB = pyrosetta.rosetta.core.select.residue_selector.ChainSelector("B")
view = sum(
    [
        viewer.init(pose),
        viewer.setStyle(cartoon_color="lightgrey", radius=0.25),
        viewer.setSurface(residue_selector=chA, colorscheme="greenCarbon", opacity=0.65, surface_type="VDW"),
        viewer.setSurface(residue_selector=chB, color="blue", opacity=1.0, surface_type="SAS"),
        viewer.setDisulfides(radius=0.25),
        viewer.setZoom(factor=1.5)
    ]
)
view()

In [ ]:
helix_selector = pyrosetta.rosetta.core.select.residue_selector.SecondaryStructureSelector("H")
sheet_selector = pyrosetta.rosetta.core.select.residue_selector.SecondaryStructureSelector("E")
loop_selector = pyrosetta.rosetta.core.select.residue_selector.SecondaryStructureSelector("L")
modules = [
    viewer.setBackgroundColor(color="grey"),
    viewer.setStyle(residue_selector=helix_selector, cartoon_color="blue", label=False, radius=0),
    viewer.setStyle(residue_selector=sheet_selector, cartoon_color="red", label=False, radius=0),
    viewer.setStyle(residue_selector=loop_selector, cartoon_color="white", label=False, radius=0)
]
view = viewer.init(poses, window_size=(1200, 600), modules=modules)
view()

In [ ]:
view.reinit() # Subtract all visualization modules previously added to the Viewer
view()

In [ ]:
# View live trajectory:
pose = pyrosetta.toolbox.pose_from_rcsb("2FD7")
view = viewer.init(pose, delay=0.15) + viewer.setStyle(radius=0.1) + viewer.setDisulfides(radius=0.1)
backrub = pyrosetta.rosetta.protocols.backrub.BackrubMover()
minimize = pyrosetta.rosetta.protocols.minimization_packing.MinMover()
for _ in range(100):
    backrub.apply(pose)
    minimize.apply(pose)
    view.show()

### Display preset custom viewers for routine visualizations:

In [ ]:
# Display preset custom viewers for routine visualizations:
viewer.presets.coreBoundarySurface(poses, window_size=(800, 600), continuous_update=True)

In [12]:
viewer.presets.ligandsAndMetals(pose, window_size=(800, 600), continuous_update=True)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

### Contribute your custom preset visualizations to PyRosetta:
 1. Edit ~Rosetta/main/source/src/python/PyRosetta/src/pyrosetta/distributed/viewer/presets/\_\_init\_\_.py 
 2. Copy and modify the "templatePreset" function, renaming it to the name of your new preset Viewer ("myCustomPreset" in step #4).
 3. Add the name of your new preset Viewer to the \_\_all\_\_ list.
 4. Merge Github pull request into RosettaCommons/main
 5. Example using it:
 ```
    import pyrosetta.distributed.viewer as viewer
    viewer.presets.myCustomPreset(poses, window_size=(800, 600), continuous_update=True)
 ```

In [16]:
def myCustomPreset(packed_and_poses_and_pdbs=None, *args, **kwargs):
    """
    Add a description of the preset Viewer here
    """
    # Add custrom ResidueSelectors
    metals_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
         pyrosetta.rosetta.core.chemical.ResidueProperty(31)
    )
    ligands_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
         pyrosetta.rosetta.core.chemical.ResidueProperty(2)
    )
    
    # Add custom Viewer commands
    view = viewer.init(packed_and_poses_and_pdbs=packed_and_poses_and_pdbs, *args, **kwargs) \
        + viewer.setBackgroundColor("white") \
        + viewer.setStyle(style="stick", colorscheme="lightgreyCarbon", radius=0.15) \
        + viewer.setStyle(residue_selector=ligands_selector, style="stick", colorscheme="brownCarbon", radius=0.5, label=True) \
        + viewer.setStyle(residue_selector=metals_selector, style="sphere", colorscheme="chainHetatm", radius=1.5, label=True) \
        + viewer.setHydrogenBonds() \
        + viewer.setDisulfides(radius=0.15) \
        + viewer.setHydrogens(color="white", radius=0.033, polar_only=True) \
        + viewer.setSurface(residue_selector=ligands_selector, surface_type="VDW", opacity=0.5, color="magenta") \
        + viewer.setSurface(residue_selector=metals_selector, surface_type="VDW", opacity=0.5, color="magenta") \
        + viewer.setZoomTo(residue_selector=ligands_selector)

    return view()

myCustomPreset(pose)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol